In [10]:
#To import all required modules

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from ttp import ttp
from pyspark.sql import SparkSession
from pyspark.conf import SparkConf
from os import path
from wordcloud import WordCloud, STOPWORDS, ImageColorGenerator

In [14]:
#to inite spark session
spark = SparkSession.builder.appName("data-cleaning").config("spark.master", "local").getOrCreate()


In [31]:
#To import the data using read function, include header, reterive schema, and separate data by \t
file_path = "tweets.csv"
tweetsDF = spark.read.csv(file_path, header=True, inferSchema=True, sep="\t")

In [32]:
#To show the data frame schema using printSchema() method
tweetsDF.printSchema()

root
 |-- text: string (nullable = true)
 |-- label: string (nullable = true)
 |-- numberOfAnnotators: integer (nullable = true)



In [33]:
#To show first five records in tweets data frame using show() method
tweetsDF.show(5)

+--------------------+-------+------------------+
|                text|  label|numberOfAnnotators|
+--------------------+-------+------------------+
|Beats by Dr. Dre ...|   spam|                 4|
|RT @Papapishu: Ma...|abusive|                 4|
|It is time to dra...| normal|                 4|
|if you notice me ...| normal|                 5|
|Forget unfollower...| normal|                 3|
+--------------------+-------+------------------+
only showing top 5 rows



In [34]:
#To show columns name
tweetsDF.columns

['text', 'label', 'numberOfAnnotators']

In [41]:
#To show number of records 
tweetsDF.count()

99996

In [77]:
#To add an id for each tweet
tweetsDF.createOrReplaceTempView('tweets')
tweets_with_id_df = spark.sql('select * from tweets')

tweets_dataset_v1 = tweets_with_id_df.toPandas()
tweets_dataset_v1.insert(0, 'id', range(1, 99997))
tweets_dataset_v1.to_csv('tweets_dataset_v1.csv')
tweets_dataset_v1.head(5)

id                                               text    label  \
0   1  Beats by Dr. Dre urBeats Wired In-Ear Headphon...     spam   
1   2  RT @Papapishu: Man it would fucking rule if we...  abusive   
2   3  It is time to draw close to Him &#128591;&#127...   normal   
3   4  if you notice me start to act different or dis...   normal   
4   5  Forget unfollowers, I believe in growing. 7 ne...   normal   

   numberOfAnnotators  
0                   4  
1                   4  
2                   4  
3                   5  
4                   3

In [79]:
#Now, we import new dataset and extract links, tags, user name and text 
#generate dataframe with id and extracted information  

file_path2 = "tweets_dataset_v1.csv"
tweets_DF_v1 = spark.read.csv(file_path2, header=True, inferSchema=True)

tweets_DF_v1.printSchema()
tweets_DF_v1.show(5)

root
 |-- _c0: integer (nullable = true)
 |-- id: integer (nullable = true)
 |-- text: string (nullable = true)
 |-- label: string (nullable = true)
 |-- numberOfAnnotators: string (nullable = true)

+---+---+--------------------+-------+------------------+
|_c0| id|                text|  label|numberOfAnnotators|
+---+---+--------------------+-------+------------------+
|  0|  1|Beats by Dr. Dre ...|   spam|                 4|
|  1|  2|RT @Papapishu: Ma...|abusive|                 4|
|  2|  3|It is time to dra...| normal|                 4|
|  3|  4|if you notice me ...| normal|                 5|
|  4|  5|Forget unfollower...| normal|                 3|
+---+---+--------------------+-------+------------------+
only showing top 5 rows



In [137]:
#To proccess text data and extract information:
tweets_DF_v1.createOrReplaceTempView('parsing_table')
onlyText_df = spark.sql("SELECT id, text FROM parsing_table")





In [144]:
#To use tweets Text module to get link, tag, and text from tweet texts
tweetsParser = ttp.Parser()
#urlsFile = open("wordCountUrls.txt", "w")
#for url in urls:
    #try:
      #  urlsFile.write(url)
      #  urlsFile.write("\n")
   # except:
       # continue


only_mytext = open("only_text.txt", "w")
only_urls = open("only_urls.txt", "w")
only_hashtags = open("only_hashtags.txt", "w")
only_users = open("only_users.txt", "w")

df = onlyText_df.toPandas()

for i, j in (df.iterrows()): 
    
    try:
        
        result = tweetsParser.parse(j[1])
        if(len(result.tags)>=1):
            for tag in result.tags:
                print(j[0],"\t",tag)

    except:
        continue
        
  



8 	 heart
8 	 cancer
15 	 TOTP
22 	 Kyrgyzstan
22 	 Kyrgyz
30 	 KhaidiNo150
30 	 ajith
43 	 XRIM
43 	 MONEY
46 	 PapuaNewGuinea
46 	 BarrickGold
47 	 Woman
47 	 Ahmedabad
50 	 Farmville2
50 	 Farmville2Info
55 	 AutumnLeaves
55 	 Photography
58 	 fishermentokings
60 	 Data
60 	 TheGoonies
63 	 KeepThemEngaged
68 	 drawntodeath
78 	 Tour
78 	 BuenosAires
78 	 BikeMountainBikeTours
79 	 HELP
80 	 tcnz2017
80 	 techcomm
80 	 ux
80 	 welovestationery
82 	 fishing
82 	 giveaway
86 	 DigitalEconomy
94 	 BBNAIJA
95 	 worldNews
101 	 notfair
102 	 reading
102 	 GlovesOn
103 	 beauty
103 	 cosmetics
103 	 makeup
104 	 keepdemocracyalive
105 	 KindlePriceDrop
108 	 MakeMoneyOnline
115 	 AppleWatch
123 	 NationalBeerDay
128 	 inthemusicnews
129 	 iHeartCountryVIP
131 	 plattinrocks
137 	 TBT
138 	 MIAMI
138 	 NYC
138 	 HOUSTON
138 	 CANADA
151 	 TheWalkingDead
151 	 TheWalkingDead
154 	 Wrestlemania
165 	 Blondie
165 	 DavidBowie
165 	 IggyPop
169 	 Grimm
171 	 Craig
171 	 football
174 	 Brexit
1

1138 	 Pakistan
1146 	 TeachingJobs
1147 	 NowOrNever
1156 	 oliviaburton
1156 	 collezioni
1163 	 TreCru
1170 	 cumfest
1174 	 hiring
1174 	 OverlandPark
1174 	 Hospitality
1177 	 hiring
1177 	 Concord
1190 	 JunoAwards
1193 	 JustWhy
1193 	 WhyMakeThingsSoDifficult
1195 	 CoachPurseDramaQueen
1195 	 WestHartford
1195 	 Rock
1196 	 Iscored
1197 	 Underground
1197 	 MixMasterAce
1197 	 ReelInTheField
1200 	 BREAKING
1212 	 HustleTown
1217 	 AFCvWHU
1217 	 SWATOT
1219 	 UniBilaWorry
1220 	 Globalbuzzlive
1233 	 facebookdeveloper
1235 	 MansionElan
1236 	 KenyanPolitics
1242 	 Actor
1242 	 DVD
1242 	 BenAffleck
1242 	 JenniferGarner
1246 	 LIVsaturdays
1249 	 sportsmassage
1249 	 curling
1253 	 Repost
1262 	 PaidTraffic
1262 	 MusicProducers
1262 	 Beatmakers
1263 	 ComingThru
1263 	 DriveIn
1263 	 TGIF
1269 	 BigData
1273 	 business
1282 	 BlueIce
1284 	 TreCru
1286 	 itgetsworseSHOW
1291 	 NFL
1291 	 Apparel
1291 	 Ravens
1292 	 TreCru
1296 	 venture
1296 	 incubator
1298 	 hot
1298 	 

2651 	 EqualPayDay
2652 	 lonewolf
2656 	 vision
2656 	 leadbiz
2661 	 WondersoftheWorld
2663 	 violence
2666 	 NowPlaying
2676 	 BBCAN5
2682 	 Storify
2682 	 OurEPA
2683 	 Psychiatry
2683 	 HumanRights
2683 	 SuicideAwareness
2689 	 Journeyto288
2691 	 PWA
2694 	 TreCru
2699 	 sorryharry
2699 	 chainsmokersare
2701 	 NEW
2701 	 Musik
2701 	 japan
2701 	 INFORMATION
2707 	 marketing
2727 	 ChiMobilizes
2733 	 justchillbeatProd
2733 	 SoundCloud
2733 	 np
2734 	 breadthofskills
2741 	 freedom
2749 	 tcot
2749 	 tlot
2749 	 ccot
2753 	 NBARooks
2757 	 MaxMosley
2757 	 dothehonourablethingandresignTom
2760 	 Easter_LIVEAtAfrikaShrine
2765 	 CancerSupport
2765 	 JoinTheFight
2766 	 supergiant
2771 	 america
2771 	 film
2772 	 NELeg
2773 	 FOSTER
2773 	 RESCUE
2773 	 Pledge
2773 	 Adopt
2781 	 WednesdayWisdom
2786 	 LetMeCheerYouUpBy
2786 	 God
2791 	 BBCAN5
2792 	 marketingautomation
2799 	 westsidespawns
2807 	 hiring
2807 	 job
2807 	 Sales
2807 	 Chandler
2813 	 saam
2813 	 resist
2813 

4166 	 BreakingNews
4168 	 pmac17
4170 	 ShedofTheYear
4182 	 Headline
4187 	 Cybersecurity
4187 	 security
4188 	 socialmedia
4204 	 R6S
4204 	 RainbowSix
4204 	 RainbowSixSiege
4204 	 WALLBANG
4206 	 hypnotherapy
4206 	 hypnosis
4207 	 giveaway
4212 	 Northumberland
4212 	 ItsInOurNature
4217 	 basketball
4219 	 Camco
4222 	 AmexHiltonGC
4223 	 BIGOLIVE
4223 	 girl
4226 	 Gospel
4226 	 hng
4229 	 itgetsworseSHOW
4234 	 np
4234 	 SoundCloud
4236 	 ImpeachTrump
4238 	 IoT
4238 	 bigdata
4238 	 digitaltransformation
4241 	 dangerous
4243 	 TrumpRussia
4244 	 GoldCoastBulletin
4244 	 goldcoastbulletin
4248 	 Olympic
4248 	 Japan
4248 	 Tokyo
4248 	 Olympics
4254 	 Brooches
4254 	 Pins
4255 	 pop
4255 	 rock
4255 	 dance
4255 	 np
4258 	 handmade
4258 	 etsy
4258 	 shopping
4258 	 decor
4264 	 steampunk
4275 	 WishfulThinking
4279 	 Entrepreneurship
4286 	 ISIS
4286 	 Trump
4287 	 MAGA
4289 	 trumpleaks
4289 	 trumprussi
4296 	 Weather
4296 	 Manchester
4296 	 MyWeather
4297 	 DeltaAliveC

5736 	 Dallas
5736 	 Texas
5737 	 WonderCrew
5739 	 BeTheNew
5742 	 mhealth
5742 	 digitalhealth
5747 	 fintech
5747 	 marketplace
5747 	 lending
5751 	 bigtits
5751 	 naked
5751 	 xxx
5753 	 TreCru
5766 	 clashroyalegemtool
5766 	 gemmesclashroyale
5779 	 Islam
5779 	 religion
5785 	 NXTTakeOverOrlando
5785 	 WWE
5785 	 NXT
5787 	 FlatEarth
5787 	 GangBang
5787 	 Redheads
5788 	 WithRefugees
5788 	 NoLostGenerationConference
5789 	 happyplace
5789 	 vibes
5791 	 crude
5791 	 oil
5791 	 Brent
5791 	 WTI
5804 	 MUSIC
5804 	 ExaltTheKingByAtonyeDouglas
5807 	 MAGA
5807 	 RussianBot
5810 	 ass
5814 	 steam
5814 	 giftcard
5814 	 free
5816 	 FirstDates
5819 	 Entrepreneur
5819 	 Mindset
5819 	 Quotes
5820 	 TreCru
5822 	 ListenLive
5822 	 NickyBlackmarket
5822 	 DrumAndBass
5824 	 journalism
5830 	 bitcoin
5831 	 icare
5832 	 billboard
5834 	 FamilyMatters
5835 	 Marketing
5835 	 DigitalMarketing
5838 	 OklahomaCity
5844 	 ACMs
5844 	 forevercountry
5844 	 musicmaker
5845 	 Residential
585

...

94176 	 FindMeInTheKingdom
94178 	 anal
94183 	 cutiesaturday
94193 	 cybersecurity
94193 	 infosec
94196 	 emarketing
94196 	 socialmedia
94199 	 Win
94199 	 giveaway
94199 	 chocolate
94205 	 Wrestlemania
94212 	 Football
94214 	 LetsG
94215 	 WildCATS
94217 	 NowOrNever
94219 	 AmazingTips
94223 	 Wrestlemania33
94229 	 Laylagabiandluis
94229 	 Chaturbate
94231 	 Vegan
94234 	 Calgary
94234 	 AlbertaTheatreProjects
94238 	 NowOrNever
94242 	 TreCru
94245 	 Somalia
94259 	 WorkFromHome
94265 	 TalMud
94266 	 48hrsInTheHub
94267 	 bookcase
94267 	 shelves
94267 	 upcycledfurniture
94268 	 AFCCup2017
94270 	 writing
94291 	 1nt
94292 	 bridal
94292 	 handmade
94296 	 susanrice
94297 	 Englandhour
94300 	 727TourKualaLumpur
94301 	 FightTheocracy
94306 	 shoes
94311 	 Weathercloud
94318 	 singapura
94322 	 Dogging
94322 	 OutdoorSex
94322 	 CarSex
94322 	 Uk_Sex
94322 	 Sluts
94322 	 GangBang
94331 	 modernslavery
94332 	 MLB
94332 	 Baseball
94332 	 LosAngeles
94332 	 Angels
94336 	 Pr

95673 	 Periscope
95686 	 ltsYourMom
95688 	 Giuseppe
95689 	 firethefools
95694 	 Finance
95702 	 venezuela
95702 	 mlbxespn
95703 	 disposableplates
95714 	 pittsburgh
95714 	 norwich
95714 	 virginia
95723 	 Art
95723 	 Painting
95723 	 Reddit
95723 	 Livebroadcasting
95724 	 WAF
95724 	 military
95724 	 Women
95726 	 SmartassSaturday
95728 	 fanslistupdated
95729 	 wedding
95733 	 EntertainmentMedia
95735 	 ytl
95740 	 MoSenate
95742 	 Smule
95742 	 SingKaraoke
95756 	 TreCru
95760 	 SyriaCharity
95760 	 Russia
95760 	 EndImpunity
95760 	 Syria
95773 	 Business
95773 	 Marketing
95788 	 Scandal
95792 	 flowers
95792 	 spring
95792 	 springtime
95794 	 lunchmenu
95794 	 springinfullswing
95794 	 r23
95794 	 loveleam
95795 	 bitcoin
95800 	 BREAKING
95800 	 9News
95805 	 emaillist
95810 	 Smule
95810 	 SingKaraoke
95813 	 Trump
95813 	 horror
95813 	 thriller
95814 	 ggfsummit17
95818 	 CrossConcert
95821 	 DRAGONTALES
95821 	 BuyAShirtChangeTheWorld
95822 	 Indians
95824 	 LittyPalo

96925 	 EDM
96925 	 dancemusic
96926 	 WashingtonNationals
96926 	 GoNationals
96926 	 Nats
96930 	 HarryPotter
96930 	 HogwartsHaggadah
96930 	 PotterPesach
96942 	 AprilFoolsDay
96947 	 maryland
96947 	 energy
96949 	 food
96949 	 recipe
96949 	 blog
96949 	 healthy
96950 	 beauty
96950 	 makeup
96950 	 skincare
96956 	 GameInsight
96956 	 ParadiseIsland2
96964 	 resconf17
96969 	 Giveaway
96969 	 CoinDrop
96971 	 Travel
96971 	 Philippines
96971 	 palawan
96972 	 WrestleMania
96974 	 LastWord
96974 	 NicholasGoldberg
96981 	 2Guys
96983 	 IGVFREE
96984 	 hiring
96984 	 Addison
96984 	 Sales
96985 	 DatingTipsForMen
96985 	 RT
96991 	 TreCru
96992 	 WWE
96992 	 WWEHOF
96995 	 NowWeRun
96998 	 foundatsimon
96998 	 giveaway
97000 	 unfinishedbusiness
97007 	 DolanTwinsNewVideo
97008 	 FifthHarmony
97008 	 YouKnowYouLoveThem
97011 	 BryanBickell
97011 	 Hurricanes
97011 	 NHL
97014 	 Coral
97015 	 NoNewContract
97015 	 WengerOut
97023 	 Latest
97024 	 MyFavoriteComebackIs
97026 	 World


98417 	 FollowFriday
98430 	 infosec
98431 	 369hong
98441 	 FiLTHYFiLTH
98442 	 elevenseshour
98457 	 Edsheeran
98457 	 excited
98462 	 WritersBlock
98472 	 music
98483 	 firemen
98487 	 SociallyAwesomeTPIR
98495 	 poundtown
98495 	 properlyfucked
98496 	 Atlanta
98496 	 I85
98496 	 I85collapse
98504 	 blood
98509 	 BoardKings
98511 	 UNF
98511 	 Donate
98511 	 SupportCause
98514 	 TwerkOrDie
98514 	 TTUThursdays
98514 	 Pantherpooloza
98514 	 GSU
98517 	 NBA
98521 	 Liverpool
98522 	 Wankamania
98523 	 trump
98523 	 nyc
98525 	 solo
98525 	 lgv20
98528 	 Live
98528 	 NP
98528 	 HipHop
98528 	 Rap
98533 	 binge
98538 	 DesiBeautyStar
98538 	 WhatIsSexy
98544 	 MAGA
98544 	 DrMartyFox
98546 	 job
98546 	 Hospitality
98546 	 Atlanta
98546 	 Veterans
98547 	 smashwords
98555 	 MachoManRandySavage
98555 	 OhYeah
98555 	 DigIt
98555 	 SupportIndyWrestling
98556 	 android
98556 	 gameinsight
98559 	 ABRArts
98560 	 USA
98560 	 Google
98566 	 ThankYouTaker
98566 	 Fan
98566 	 ThenNowForever


99668 	 Whore
99668 	 CumSlut
99668 	 MILF
99673 	 resist
99676 	 OneDorection
99676 	 YouKnowYouLoveThem
99681 	 ChaoticHouseParty
99683 	 ConfirmGorsuch
99683 	 PJNET
99687 	 ItStopsNow
99691 	 Easter
99691 	 Easterweekend
99693 	 Joinup
99693 	 ISA2
99695 	 jesus
99696 	 R116
99700 	 hiring
99700 	 job
99705 	 kenzie
99712 	 icymi
99712 	 breaking
99715 	 OneDirection
99715 	 YouKnowYouLoveThem
99718 	 NP
99718 	 JujuVibesContinua
99718 	 1049SMAFM
99719 	 NoDapl
99725 	 sunsetstroll
99725 	 eveningstroll
99725 	 paris
99726 	 Low
99726 	 housing
99732 	 SlowWhiteguy
99747 	 Uber
99751 	 SUPERSTARLIFE
99754 	 OneDirection
99754 	 YouKnowYouLoveThem
99757 	 Bingo
99757 	 Lookbingo
99758 	 miracle
99758 	 jesus
99761 	 Indeed
99761 	 jobs
99763 	 TreCru
99767 	 MiamiHeat
99767 	 Heat
99771 	 MarchSadness
99785 	 TheSarahSimmonsBand
99789 	 mypic
99795 	 Trump
99795 	 Regan
99800 	 2A
99808 	 mockups
99810 	 DateMyFamily
99811 	 MakingmoneywithForex
99811 	 Forex
99811 	 MoneyMaking
99

In [146]:
for i, j in (df.iterrows()): 
    
    try:
        
        result = tweetsParser.parse(j[1])
        if(len(result.urls)>=1):
            for url in result.urls:
                print(j[0],"\t",url)
    except:
        continue


1 	 https://t.co/9tREpqfyW4
1 	 https://t.co/FCaWyWRbpE
3 	 https://t.co/MVRBBX2aqJ
5 	 https://t.co/bunPHQNXhj
7 	 https://t.co/N7LE8lX7Rm
8 	 https://t.co/2TLawmHhEe
9 	 https://t.co/niSeJrLKHq
11 	 https://t.co/ZLmrbf6S3O
11 	 https://t.co/v4IdDN4hvu
12 	 https://t.co/2QLmn3tIjf
14 	 https://t.co/lkYGXODb5P
17 	 https://t.co/AhapGJ3WAb
21 	 https://t.co/eT4D2ClsT3
23 	 https://t.co/FOWMKFEF6U
24 	 https://t.co/sDL66x8e7Z
25 	 https://t.co/Jo2UvZjOJM
25 	 https://t.co/nG5UWyAxs2
27 	 https://t.co/GhSTgNHWxS
27 	 https://t.co/onc8bySr62
28 	 https://t.co/T8EzLoH90K
28 	 https://t.co/8hE1EFpkMY
29 	 https://t.co/R7j609MsQs
30 	 https://t.co/fuSiKpb5t1
33 	 https://t.co/wKxOtbDFl5
34 	 https://t.co/c7KWWKSM4Y
36 	 https://t.co/TSuRXiqGnP
38 	 https://t.co/fHX8y7esMH
39 	 https://t.co/xV8cqszq7i
43 	 https://t.co/6H1M2b2GQz
44 	 https://t.co/cpvKXrGUn9
46 	 https://t.co/7bbF85xlhP
50 	 https://t.co/D4SZzsHa70
50 	 https://t.co/zW6Ce2rE0X
51 	 https://t.co/MuPKIhR1oN
51 	 https://t.co/klx

509 	 https://t.co/sHCTbJmgeU
510 	 https://t.co/3CQaIpa3Go
510 	 https://t.co/Q92jOXdQgI
511 	 https://t.co/G15T5W6zar
511 	 https://t.co/6YWvZUkRqB
512 	 https://t.co/6RqPz75caU
512 	 https://t.co/KuGxyMInW2
514 	 https://t.co/kY766nk6X5
515 	 https://t.co/LyZMuQETLg
519 	 https://t.co/UrVL34ZzQ4
521 	 https://t.co/Wr9onAYEB3
524 	 https://t.co/dSHNC6v77e
525 	 https://t.co/EkZmoPYkt0
525 	 https://t.co/3kO9OSE3KR
526 	 https://t.co/uUebFW3r4t
527 	 https://t.co/M6TBAYVHn7
528 	 https://t.co/Nym01YXi0j
528 	 https://t.co/Ss8jLooUwG
529 	 https://t.co/Tnk2Cert4G
531 	 https://t.co/smXiKLURRp
532 	 https://t.co/sP364bm53E
533 	 https://t.co/1sNGPuDnqc
534 	 https://t.co/EY6STLARQP
534 	 https://t.co/BvKl9myy3x
535 	 https://t.co/3NS3HFD4P3
536 	 https://t.co/9vquYPNxbU
536 	 https://t.co/OLLKm2Asgk
536 	 https://t.co/qj4VJrFVbF
536 	 https://t.co/VLaKPylNJQ
537 	 https://t.co/95D45822Nm
538 	 https://t.co/tSZYjl527Z
539 	 https://t.co/cY2fuArV5h
540 	 https://t.co/QXZMPETRsK
540 	 http

1052 	 https://t.co/i5J0GiDEMj
1052 	 https://t.co/GD38LN8w53
1054 	 https://t.co/5oV6PAQzJD
1056 	 https://t.co/W9XwEcOMRL
1057 	 https://t.co/aCkV7DLgBP
1058 	 https://t.co/ZrXTM6L7RK
1059 	 https://t.co/SXTZ24Ucyd
1061 	 https://t.co/0zn0Hl1fPA
1062 	 https://t.co/JEGXMmj
1063 	 https://t.co/1k3bRCpzHF
1065 	 https://t.co/PST0SWsb9B
1067 	 https://t.co/U03QhiXYRI
1067 	 https://t.co/GPhFkuHFRN
1068 	 https://t.co/nBYvRBXeNo
1073 	 https://t.co/W5FC6GLq8F
1075 	 https://t.co/SMfJeD7ut4
1078 	 https://t.co/m5fPR5Iyp5
1078 	 https://t.co/RveR3Ejc8A
1079 	 https://t.co/h9NnrSPZhm
1080 	 https://t.co/GW6IyCUlGO
1081 	 https://t.co/Pb5s3VP1Xg
1082 	 https://t.co/XsZEraTlSE
1084 	 https://t.co/rS6s7YzWd2
1084 	 https://t.co/lfIOEdANNi
1085 	 https://t.co/SKvXayFBHC
1086 	 https://t.co/rc1RF0dSJ5
1086 	 https://t.co/cYMdTOWv5h
1087 	 https://t.co/JoKDPBQr58
1088 	 https://t.co/6VIxyUZRj4
1088 	 https://t.co/clc6PxrdN5
1089 	 https://t.co/5dWPk4TG0Y
1095 	 https://t.co/v5vA51tcnr
1096 	 http

1539 	 https://t.co/Bq6n9hiAsf
1540 	 https://t.co/6iMOl86pGc
1542 	 https://t.co/Ul3c3NblKo
1544 	 https://t.co/FhpG0PzaBl
1545 	 https://t.co/j9ZEv3bEOG
1549 	 https://t.co/FaXtdx6KVl
1551 	 https://t.co/UBO3P8yk7r
1551 	 https://t.co/4a09plydtE
1552 	 https://t.co/lbusEaIQCF
1554 	 https://t.co/Rv5bXtMIWh
1555 	 https://t.co/oQDG5BkR2B
1558 	 https://t.co/c6nOfpFGfq
1559 	 https://t.co/duuHonfdDo
1560 	 https://t.co/fOakkrvFcR
1560 	 https://t.co/FbXNkX6YG9
1561 	 https://t.co/db6OpgB4qI
1562 	 https://t.co/ebG41dfzwN
1563 	 https://t.co/edieiGapjw
1566 	 https://t.co/CcSQvWViD4
1567 	 https://t.co/U3fJqxxwMj
1568 	 https://t.co/E4nTORQYim
1568 	 https://t.co/3dVH7JDrJ6
1570 	 https://t.co/DJc30IPz22
1570 	 https://t.co/ZuXoKTXtiw
1571 	 https://t.co/hKYyBlnuYA
1572 	 https://t.co/O9EAifnuQa
1573 	 https://t.co/u9lhHeJERI
1574 	 https://t.co/5jQw7mJtpW
1577 	 https://t.co/VWY6lL66Mo
1578 	 https://t.co/e7cpRR5v8y
1579 	 https://t.co/bNQIabDgj8
1580 	 https://t.co/ySF2YhaLL3
1580 	 h

2094 	 https://t.co/jdj8M94A4A
2094 	 https://t.co/67J6AkRL50
2095 	 https://t.co/um9zxVhRTH
2095 	 https://t.co/NMS8xunWh8
2096 	 https://t.co/ktBoXZb2iB
2098 	 https://t.co/0Tf555lkmn
2100 	 https://t.co/9p5tIcmNiD
2100 	 https://t.co/N9Ru0MK9mp
2101 	 https://t.co/hEk00mNQGM
2101 	 https://t.co/owB8meljkV
2102 	 https://t.co/sVMVM2RzGN
2103 	 https://t.co/Sbg1ZwLHgk
2103 	 https://t.co/m0VWvXbQ66
2105 	 https://t.co/15r2sXoWwn
2110 	 https://t.co/jgczrevo9Q
2112 	 https://t.co/RbbWzjIPfi
2113 	 https://t.co/DyXylTvoai
2113 	 https://t.co/eJM3hZjtSV
2114 	 https://t.co/6R5Sywn6Br
2115 	 https://t.co/W8RYCQfdoM
2116 	 https://t.co/bwYpmh2Xlt
2117 	 https://t.co/YOSMCIixwg
2119 	 https://t.co/dTe0GJVooY
2120 	 https://t.co/dJbTwFTZrh
2121 	 https://t.co/z4oxMlhDJe
2121 	 https://t.co/TQZocPZKVV
2122 	 https://t.co/GKyJESiNLp
2123 	 https://t.co/gdyzaUPr4V
2124 	 https://t.co/Jc2keQCa1K
2125 	 https://t.co/OFM7GSd6uk
2127 	 https://t.co/lowbqRTBSG
2128 	 https://t.co/FzTIA
2129 	 https:

...

97767 	 https://t.co/LacS8gft6G
97768 	 https://t.co/TFYmK3NrLi
97769 	 https://t.co/APLZna49Ea
97772 	 https://t.co/CGgXJpYG65
97773 	 https://t.co/SCgSBVPXOL
97775 	 https://t.co/BBvY0EBdEi
97775 	 https://t.co/PffRasBfXj
97776 	 https://t.co/BIAXsF6Zy0
97776 	 https://t.co/w3e8SAzkSL
97777 	 https://t.co/v9ng3S1OoD
97778 	 https://t.co/SbCQ1NT8G7
97779 	 https://t.co/avJyHehfPX
97783 	 https://t.co/nLv3vtxzmp
97786 	 https://t.co/2go0JSNrpZ
97787 	 https://t.co/yUaYBzx
97789 	 https://t.co/2ZDpWJkI33
97790 	 https://t.co/4SDt79gX9N
97792 	 https://t.co/dN23IXVxn3
97793 	 https://t.co/a7VK8xvWtj
97794 	 https://t.co/CFkhGjM391
97797 	 https://t.co/DmbbaFHAKI
97797 	 https://t.co/5iEfFC3Jro
97799 	 https://t.co/aR0tIdaLBK
97800 	 https://t.co/mB8EGHe9HF
97800 	 https://t.co/Ye9SYK0u4Z
97801 	 https://t.co/H1bN33Mcn9
97803 	 https://t.co/AgiLDFc4fN
97804 	 https://t.co/6it4poo170
97806 	 https://t.co/KrZZclm9nP
97807 	 https://t.co/Are5c44cXu
97810 	 https://t.co/fI2oTV2ry8
97813 	 htt

98239 	 https://t.co/LpUMwzcN5a
98240 	 https://t.co/WabclVn0z9
98241 	 https://t.co/x0jnNwlmKC
98243 	 https://t.co/UvHM4sqE2Z
98243 	 https://t.co/bpGn8tBZt7
98244 	 https://t.co/xCzpV6gCTC
98244 	 https://t.co/Wn9qU8dM2v
98245 	 https://t.co/5JkHnI1uB9
98246 	 https://t.co/OtSnX8b0L3
98246 	 https://t.co/lNe1Kun3BW
98249 	 https://t.co/WtKrYhauqK
98250 	 https://t.co/RMXbYFt7mN
98251 	 https://t.co/Vl2oZFfLt1
98253 	 https://t.co/W2pRfMEc86
98257 	 https://t.co/ZNTavRMD6Y
98258 	 https://t.co/4nuDYJnqoS
98262 	 https://t.co/Oi0lOByWXs
98264 	 https://t.co/DkLIr7pLwf
98264 	 https://t.co/Sr75KJGOah
98267 	 https://t.co/Rofd8IaT3h
98268 	 https://t.co/pboGLo5cR5
98269 	 https://t.co/U7nnLcCdkI
98269 	 https://t.co/eFGvyWr1ht
98271 	 https://t.co/hY0fxEQNix
98271 	 https://t.co/NtFXPjypTz
98272 	 https://t.co/IkfE3c0vH0
98274 	 https://t.co/D8c6ge1oPY
98276 	 https://t.co/WG46q9yd5h
98277 	 https://t.co/inzzl7jRtl
98278 	 https://t.co/SNN8teneCT
98279 	 https://t.co/qRwZvXGEpr
98280 	 

98762 	 https://t.co/KkqomoPFvi
98764 	 https://t.co/y6MFGVSgiM
98765 	 https://t.co/mpi8HH9u3n
98766 	 https://t.co/mbfvDqFUwu
98767 	 https://t.co/NBrX34Llyj
98767 	 https://t.co/zg3RqiEkxq
98768 	 https://t.co/pfm0jbjyXc
98771 	 https://t.co/nJa28Mqydn
98772 	 https://t.co/l8NChXYy0d
98772 	 https://t.co/A7rQwSJjlW
98775 	 https://t.co/HvFF8jn1jR
98779 	 https://t.co/fonI0vcspq
98780 	 https://t.co/SfCudBIIKo
98780 	 https://t.co/nT7ApxQGQr
98781 	 https://t.co/fbMKG7Nw51
98782 	 https://t.co/0nSTAPo8Xo
98782 	 https://t.co/TpCXtRhFuR
98786 	 https://t.co/uou4dAWiDk
98787 	 https://t.co/TRAb298Lg6
98788 	 https://t.co/zS0UMQGw7e
98790 	 https://t.co/R8jaSEs6Tm
98790 	 https://t.co/CRzcMT2gvc
98791 	 https://t.co/lxdXagIF2W
98793 	 https://t.co/7GeTN8skzb
98794 	 https://t.co/iYyUGNi7Qy
98795 	 https://t.co/k2nMtNRiMi
98800 	 https://t.co/kxtKhy9sGH
98802 	 https://t.co/wCy0cE2ffO
98802 	 https://t.co/VeiOVUznzL
98803 	 https://t.co/OmKIBu3uK4
98804 	 https://t.co/bY3f6Df1H5
98804 	 

99275 	 https://t.co/jo2122oq69
99276 	 https://t.co/RwejllvtuH
99278 	 https://t.co/zNNoHHXzO6
99279 	 https://t.co/FzTIA
99280 	 https://t.co/F8T3GXjbOT
99280 	 https://t.co/7dfHdjT60J
99281 	 https://t.co/aSURzppMS3
99283 	 https://t.co/cPa9kyIRXF
99285 	 https://t.co/YhrxIMwz2v
99287 	 https://t.co/seeuXxUS3Y
99289 	 https://t.co/o4WO7bwHAL
99290 	 https://t.co/ggUuDZlAB5
99291 	 https://t.co/QD1o36haeh
99291 	 https://t.co/d2zgWCCHLn
99292 	 https://t.co/LpUMwzcN5a
99293 	 https://t.co/NJ5JxjL6E9
99296 	 https://t.co/qKH9qrs3W6
99302 	 https://t.co/ZHP560pLcf
99304 	 https://t.co/dPr7lZlCsV
99305 	 https://t.co/Z33ltwVgfc
99306 	 https://t.co/sv50j1CF0d
99307 	 https://t.co/ywKDbR6kMS
99308 	 https://t.co/n1H1eAh33F
99311 	 https://t.co/8wRJ
99312 	 https://t.co/ZL9PyPJtu6
99312 	 https://t.co/GzZmjifZmv
99314 	 https://t.co/Z90GzYX5g3
99319 	 https://t.co/NGZioU8ZVO
99319 	 https://t.co/XiGiiYJCpm
99320 	 https://t.co/Au9TpG9sRT
99321 	 https://t.co/xNMWQfNPmt
99323 	 https://t.c

99800 	 https://t.co/rdodNGCKlz
99801 	 https://t.co/LA052uVT26
99801 	 https://t.co/L8Rg3C5r6m
99808 	 https://t.co/jAKCYSPmgF
99811 	 https://t.co/mxmWwufsE9
99811 	 https://t.co/jZKyqGiUnh
99812 	 https://t.co/1BhN2ENdZ6
99814 	 https://t.co/XN6FV38IhR
99816 	 https://t.co/Z7rmNWwGEE
99816 	 https://t.co/CH2BU1bNZw
99817 	 https://t.co/nuYdAgF3A6
99818 	 https://t.co/yKZPmezMOh
99821 	 https://t.co/LNjjezj6Az
99821 	 https://t.co/WBctNh4ymo
99823 	 https://t.co/DiuY2Dass2
99823 	 https://t.co/tTOcNuT3Vx
99824 	 https://t.co/4G7sA6VNpZ
99824 	 https://t.co/WATDu92sPE
99825 	 https://t.co/GSM62sq0Nw
99826 	 https://t.co/QB0Y4O6epR
99827 	 https://t.co/FFJmGuXsl6
99828 	 https://t.co/8xQmFw7c91
99830 	 https://t.co/sHerPB31rQ
99831 	 https://t.co/BojmnQPcIm
99835 	 https://t.co/gs0fU2ZeSl
99835 	 https://t.co/XWSihc9gBq
99836 	 https://t.co/lzwsxoPdxw
99838 	 https://t.co/avXF3cYdWV
99839 	 https://t.co/rF9ZvqyDAC
99839 	 https://t.co/hmjv5OpWQv
99840 	 https://t.co/2LOqn1jOKQ
99840 	 

In [148]:
for i, j in (df.iterrows()): 
    
    try:
        
        result = tweetsParser.parse(j[1])
        if(len(result.users)>=1):
            for user in result.users:
                print(j[0],"\t",user)
    except:
        continue


2 	 Papapishu
6 	 Vitiligoprince
7 	 HighHorseGames
9 	 YouTube
9 	 mattshea
10 	 LestuhGang_
12 	 Move_Fwd
13 	 ennoia3
16 	 EiramAydni
18 	 ChrisRBarron
19 	 Evelyna_Johnson
26 	 ByYourLogic
29 	 pepsi
29 	 KendallJenner
32 	 smiilinbiig
34 	 techUK
38 	 ynaoivw
39 	 swearyexpat
40 	 iamcodyengland
42 	 TheRealMs_100
44 	 neilfinnytaylor
45 	 Joshua_Mikel
48 	 chrisspooh_13
52 	 williamlegate
52 	 FredWright48
52 	 FoxNews
52 	 JoeCurtatone
53 	 13ReasonsLife
63 	 Adil_Malia
65 	 ___angelicaaaa
67 	 Historiann
69 	 ProjetoooHelp
69 	 onedirection
69 	 radiodisney
69 	 NiallOfficial
69 	 LiamPayne
69 	 Louis_Tomlinson
69 	 Harry_Styles
70 	 NiykeeHeaton
72 	 WaysThingsWork
73 	 WatertonLakesNP
77 	 biancaquilan
79 	 AmericanAir
81 	 thequote
83 	 alaskanillusion
83 	 ShaunKing
83 	 zbleumoon
83 	 DonaldJTrumpJr
85 	 bruinz0477
87 	 Mike_Coop20
88 	 KianaYoungg
89 	 heartlle
91 	 genymets
92 	 BananaKarenina
92 	 Jezebel
93 	 jchaltiwanger
94 	 mbalsea
94 	 sheedy407
96 	 liamgallagher

708 	 favlilshawty
710 	 Shirou14
712 	 validatedroses
714 	 dpradhanbjp
716 	 jennylsq
718 	 dixonowl05
718 	 lulazarte66
718 	 Jennaswan1
718 	 wwwbigbaldhead
718 	 NormansCat
718 	 leezermae
718 	 leedusme1227
718 	 TWD_Ghost
718 	 arae_TWD
720 	 halsey
723 	 CallMe_THRASHER
725 	 KimmyCums
725 	 Gary87xxx
725 	 juicygemma247
727 	 N5ySp7FdinoTj1c
728 	 Geantvert72
729 	 YouTube
729 	 kootra
730 	 GraemeFawell
731 	 kobfm
731 	 portallovato
731 	 zaynmalik
731 	 partynextdoor
731 	 CheatCodesMusic
731 	 ddlovato
735 	 MrChrisLeeks
738 	 nyafromfire
738 	 AfricanNimrod
738 	 SuperNjoro
738 	 MarkTerritore
738 	 Cuba_Brown
739 	 SHSLGhostBoy
740 	 KanyeOfficiaI
741 	 AndreaRussett
742 	 lexi4prez
743 	 karlaacosta22
744 	 akosiKenChan
744 	 dealwithBARBIE
746 	 HBaldwinMP
748 	 KelseaBallerini
749 	 G2esports
749 	 sOAZIZGOOD
749 	 BroxahLoL
749 	 Caps1337Mid
749 	 RekklesLoL
749 	 Jesizlol
751 	 AnneKadet
751 	 CityofYonkers
751 	 MayorMikeSpano
751 	 GenYonkers
751 	 WSJ
753 	 cjwer

1240 	 AshhV_
1244 	 Lickmy_kayy
1245 	 ChrisSweetTweet
1245 	 deedles420
1246 	 clublivmcr
1246 	 AaronSBreak
1246 	 PaigeRhiannaF
1246 	 Charjackox
1246 	 SpoonerNicola
1246 	 hollyvhewitt
1246 	 RachDale
1246 	 MoeZain
1253 	 Maxturk
1255 	 _ColeFyn
1255 	 MaczaddyK
1263 	 HeyKato
1263 	 SigalaMusic
1263 	 HaileeSteinfeld
1263 	 Ninaolebara
1264 	 GWRHelp
1267 	 garbanzoguy
1269 	 JoeMcKendrick
1271 	 mydinmalaysia
1276 	 elisabethlehem
1277 	 SquarespaceHelp
1281 	 MonarchFisher
1281 	 Damn_It_Dillon
1285 	 HoesLoveGLO
1286 	 shanedawson
1288 	 cubs
1289 	 Lmao
1290 	 undeveIoped
1293 	 realDonaldTrump
1293 	 RepMarkMeadows
1293 	 Jim_Jordan
1293 	 Raul_Labrador
1294 	 samanthajgross
1299 	 ProjetoooHelp
1299 	 onedirection
1299 	 radiodisney
1299 	 NiallOfficial
1299 	 LiamPayne
1299 	 Louis_Tomlinson
1299 	 Harry_Styles
1300 	 jessicacitifm
1301 	 Zamoraaah
1301 	 DumbPeopleAsf
1301 	 barzin25
1302 	 iBe_JP_
1306 	 neo_real_ist
1306 	 deepfriedcouch
1307 	 AblondeMinx
1309 	 stan

1823 	 JustinRaimondo
1823 	 PrisonPlanet
1824 	 liaria0068
1824 	 Aquarelle0201
1827 	 RepSpeier
1827 	 POTUS
1829 	 fujifilm
1830 	 nardybadazzent4
1831 	 warnetony
1832 	 DrZiro
1832 	 SiderPress
1832 	 HowleyMichael
1832 	 perriOHS
1834 	 Dory
1836 	 AOL
1839 	 DevinNunes
1840 	 issabhadie
1841 	 jlangdale
1841 	 evelynnfarkas
1841 	 MSNBC
1847 	 RiceGum
1849 	 13ReasonsLife
1850 	 untappd
1851 	 mrtstur
1851 	 BlogLiberally
1852 	 JeremyWGR
1854 	 paulsteele1979
1854 	 Keir_Starmer
1854 	 jeremycorbyn
1855 	 chy_leigh
1856 	 HBMAKINOUT
1857 	 oliviagobrien
1858 	 kpopasanime
1859 	 SaffronBarker
1860 	 Lanna_1219
1861 	 SweatyBucket
1861 	 IsLuxcy
1864 	 SuttonOfficial
1865 	 TeamEmmmmsie
1865 	 TeamEmmmmsie
1866 	 WrassleRap
1869 	 kayhihello
1870 	 ladyluvlylocs
1872 	 auranoir
1878 	 LJobling96
1879 	 AndyRichter
1880 	 whotfislarry
1883 	 DetonicsMKV
1883 	 Bodytalk_Now
1884 	 RCGibby73
1884 	 Bernardine
1884 	 XVCrosstrek
1884 	 eddieG805
1884 	 shawnmanogue
1887 	 WYOPhil
18

2518 	 rg06sss_
2518 	 lewisc_00
2518 	 paul_r1986
2520 	 MannyMua733
2521 	 usernamePhan
2523 	 desichorii1
2524 	 SocialistVoice
2524 	 Archie_Simpson_
2525 	 ABCNews
2529 	 Ankineedu1A
2529 	 WoCharLog
2529 	 laxman_xy
2530 	 YouTube
2530 	 explodingtnt
2534 	 BabyyArri
2536 	 DonnieCalabrese
2536 	 JustinTrudeau
2536 	 MatthewPerry
2541 	 KAYdashian_
2542 	 kreesholvah
2544 	 mamautistic36
2544 	 photon_barrier
2546 	 beebearninja
2546 	 SyLazovik
2546 	 booskellington
2549 	 _liveyourlegend
2549 	 TEDxGoldenGate
2550 	 EnVy_Apathy
2551 	 kaneens
2554 	 MamaSnuggles_
2559 	 jeremycorbyn
2560 	 yxngbane
2562 	 MamataOfficial
2563 	 plusnethelp
2565 	 TheBorisBecker
2566 	 SaylemTweety
2568 	 sensualgifs
2571 	 AustinGooderNN
2571 	 OSFMRosters
2572 	 Dory
2573 	 Elizabethhh____
2574 	 _jadanoele
2576 	 whotfislarry
2577 	 _JakeBrown
2577 	 Twitter
2578 	 StevieKnip
2579 	 MeliMel_82
2580 	 MonsterTit1
2587 	 PatronusMalec
2590 	 TuryTheCutiee
2592 	 YouTube
2593 	 Burmese_Tyga
2596 

...

97161 	 barry_mcgarry
97165 	 J_Nova_Kane
97167 	 swiftlyheaton
97169 	 RadioTiempo1059
97169 	 JhonJairoSilva
97169 	 cncocolombiafc
97169 	 CncoMedellinOfc
97171 	 YouTube
97171 	 Hodgetwins
97172 	 itsghetti
97173 	 POTUS
97174 	 Smook_Dawg
97180 	 CallumMcNab93
97181 	 AvaAddams
97183 	 evostikleague
97184 	 sincir3000
97185 	 VP
97185 	 POTUS
97185 	 ShopFloorNAM
97188 	 vexedmentals
97189 	 dswizzzlee
97190 	 bitetheking
97191 	 BernardNigga
97192 	 zhnogren
97193 	 ThePCCustomiser
97193 	 meganyy
97193 	 xsplit
97194 	 ehayward93
97195 	 gregjames
97197 	 TraineeGasDoc
97199 	 nextbitsys
97199 	 flipkartsupport
97200 	 HardcoreValue
97200 	 gregmaffei
97201 	 YouTube
97201 	 mrtlexify
97204 	 CerromeZONE
97205 	 nancysantillann
97208 	 djtomcrusher
97210 	 BrightonMuseums
97212 	 13ReasonsFans
97213 	 2121Savage
97214 	 Tate
97215 	 SilorBoy
97215 	 Gale1212Harriet
97218 	 sachin_rt
97218 	 IPL
97221 	 Princexercize
97222 	 NOTTODAYLIVE
97223 	 Bipartisan
97225 	 KylieDTiger
972

97787 	 nakedmagic
97790 	 LifeAsBros
97791 	 realDonaldTrump
97791 	 GOP
97791 	 SenateGOP
97791 	 HouseGOP
97793 	 StEdwardCS
97793 	 LauraDeeves
97793 	 OneNoteEDU
97794 	 CSJDujardin
97795 	 DawgDaisy
97795 	 Lin_Manuel
97796 	 jxsuke
97799 	 popcrush
97802 	 Jamiaarmani_
97804 	 ROBINS
97804 	 orenjimaru
97805 	 ABOOGlE_
97806 	 tunguz
97807 	 PatelMayank2
97807 	 beegeorge
97807 	 nikhilchinapa
97808 	 lilbabykrisatan
97809 	 AlexeiEmelin
97810 	 unlimapps
97811 	 MRMartinez4LD9
97812 	 SenRonJohnson
97812 	 RonJohnsonWI
97812 	 POTUS
97812 	 GOP
97813 	 NatShine1
97813 	 aigbe_samuel
97813 	 169enter
97814 	 riahtaughtyou
97815 	 sagedapprentice
97815 	 Proverbs3__5
97815 	 aigkenham
97816 	 oTruhmp
97820 	 bad_dragon
97821 	 jaketapper
97823 	 katyperry
97825 	 jackocfc
97825 	 vasdimovski
97825 	 lucasBrowne
97825 	 CounterPunchPC
97825 	 DillianWhyte
97826 	 YouTube
97829 	 autismspeaks
97829 	 autselfadvocacy
97830 	 tommyjhansonn
97830 	 Dobbln
97830 	 sibrow
97830 	 Benjam

98445 	 Diane4795
98445 	 Malbrenbremal
98445 	 vjmlloyd1
98446 	 politico
98447 	 Norminib_
98447 	 ismhnif
98447 	 _marinashahira
98447 	 firzanahbasar
98447 	 AlSayyidah
98448 	 NawRob
98450 	 possumash
98450 	 CastielMeAtSix
98452 	 SpeakerRyan
98457 	 ZiggoDome
98460 	 problematicjade
98461 	 YouTube
98461 	 zacksjerryrig
98462 	 TheNightWorlds
98462 	 theauthorology
98464 	 markymark930
98465 	 SunnFunFlyIn
98468 	 Aflac
98469 	 isabelaseraffim
98470 	 h3h3productions
98470 	 jacknicas
98470 	 WSJ
98470 	 WSJ
98470 	 CocaColaCo
98470 	 pepsi
98472 	 NAFME
98478 	 brexshitshmexit
98478 	 Telegraph
98479 	 G4SHI
98480 	 jessfrr
98482 	 RunsWithCrazy
98483 	 DMcglusky
98487 	 PriceIsRight
98490 	 Quixotic_Puppy
98490 	 RichardBSpencer
98492 	 2000sHlTS
98493 	 xoxo_auri
98494 	 Harry_Styles
98495 	 ThisIsKris10
98495 	 ItsMickeyTaylor
98495 	 MasonSteele94
98495 	 ColbyKnoXXX
98500 	 youngcons
98501 	 thethickway
98502 	 Kaamdizzle
98503 	 KHVH
98503 	 ScottMorishige
98503 	 Honolul

99091 	 Doorbundle
99092 	 carliejoooo
99092 	 jollygoodshoww
99092 	 124_kayla
99092 	 jackie_custer16
99092 	 fuckinglaurenk
99099 	 csydelko
99099 	 FireballWhisky
99101 	 sparklymingyu
99103 	 ProjetoooHelp
99103 	 Michael94095061
99103 	 onedirection
99103 	 radiodisney
99103 	 NiallOfficial
99103 	 LiamPayne
99103 	 Louis_Tomlinson
99103 	 Harry_Styles
99105 	 ConnieHair
99108 	 rocket_slice
99112 	 PurposeForever
99112 	 LeahRBoss
99114 	 RenegadeRoss
99116 	 melax33
99117 	 yashar
99117 	 GeraldoRivera
99117 	 ericbolling
99117 	 Ericbolling
99120 	 fIeekin
99123 	 Deadspin
99124 	 shoe0nhead
99125 	 RickyRawls
99126 	 EricDroll
99127 	 Cassius1313
99128 	 paytons_hawtmom
99130 	 YouTube
99131 	 QueenPeggles
99131 	 RichardTaylor_
99134 	 iamwilliewill
99136 	 roguebanjo
99139 	 ThatsJustOdd
99140 	 weedbees
99144 	 TheEraOfCool
99145 	 NATEGAWD
99146 	 Thelifeofmalij
99147 	 puIIingout
99150 	 nasboat
99151 	 stuart_2017
99153 	 talking
99154 	 wpbeginner
99159 	 Cam_Oflage
99

99693 	 vdbhans
99694 	 LukeHowells10
99694 	 tomlmorgan146
99697 	 eannabasketball
99697 	 emmaclancy8
99698 	 IndigoLFC
99699 	 shebainpdx
99701 	 destineybleu
99709 	 HalliKjartans
99709 	 LaloDagach
99709 	 IBoyd1966
99709 	 Red_Tints
99712 	 FerretScot
99712 	 helenrogers19c
99713 	 ryan_lamb
99715 	 ProjetoooHelp
99715 	 radiodisney
99715 	 radiodisney
99716 	 alexs_ebooks
99717 	 XOnicksX
99719 	 crhousel
99721 	 Akonsowaa
99724 	 MillerMuric
99725 	 pawsitivescoop
99728 	 2000sHlTS
99730 	 FoxNews
99731 	 SenateMajLdr
99734 	 JoyAnnReid
99735 	 godwattery
99737 	 rrangel_04
99739 	 deathpigeon
99739 	 gabrielamadej
99739 	 24bitpessimist
99739 	 Jebriel
99740 	 YouTube
99742 	 Dugout
99742 	 realmadrid
99742 	 GarethBale11
99742 	 realmadridfra
99742 	 FAWales
99743 	 NiyaButt
99745 	 nypost
99747 	 Uber_Support
99748 	 TheNoxusFemale
99749 	 PolyhedronC
99749 	 geeknson
99749 	 burning_games
99749 	 defectiongame
99754 	 ProjetoooHelp
99754 	 sotoakipelaoned
99754 	 radiodisne

In [158]:
import re
text_list = [] 

for t in onlyText_df.select("text").collect():
    rtxt = (' '.join(re.sub("(@[A-Za-z0-9]+)|([^0-9A-Za-z \t])|(\w+:\/\/\S+)"," ",str(t.text)).split())).lstrip("RT")
    if (rtxt != ""):
    
        text_list.append(rtxt)
print(len(text_list))

99864


In [159]:

mytext = pd.DataFrame(text_list)
mytext.head()

0
0  Beats by Dr Dre urBeats Wired In Ear Headphone...
1   Man it would fucking rule if we had a party t...
2  It is time to draw close to Him 128591 127995 ...
3  if you notice me start to act different or dis...
4  Forget unfollowers I believe in growing 7 new ...

In [161]:
my_id = []
for t in onlyText_df.select("id").collect():
    my_id.append(t.id)
print(len(my_id))

mytext =  pd.DataFrame(my_id)

99996


In [156]:
stopwords = set(STOPWORDS)
lol = mytext.flatMap(lambda x: x.split(" "))
myNewText = lol.filter(lambda x: x.lower() not in stopwords)

AttributeError: 'DataFrame' object has no attribute 'flatMap'